# ePix100 Dark Characterization

Author: M. Karnevskiy, Version 1.0

The following notebook provides dark image analysis of the ePix100 detector.

Dark characterization evaluates offset and noise of the detector and gives information about bad pixels. Resulting maps are saved as .h5 files for a latter use and injected to calibration DB.

In [ ]:
cluster_profile = "noDB" # ipcluster profile to use
in_folder = '/gpfs/exfel/exp/HED/202030/p900136/raw' # input folder, required
out_folder = '/gpfs/exfel/data/scratch/ahmedk/test/HED_dark/' # output folder, required
sequence = 0 # sequence file to use
run = 182 # which run to read data from, required

karabo_id = "HED_IA1_EPX100-2" # karabo karabo_id
karabo_da = ["EPIX02"]  # data aggregators
receiver_id = "RECEIVER" # inset for receiver devices
path_template = 'RAW-R{:04d}-{}-S{{:05d}}.h5' # the template to use to access data
h5path = '/INSTRUMENT/{}/DET/{}:daqOutput/data/image/pixels' # path in the HDF5 file to images
h5path_t = '/INSTRUMENT/{}/DET/{}:daqOutput/data/backTemp'  # path to find temperature at
h5path_cntrl = '/CONTROL/{}/DET'  # path to control data

use_dir_creation_date = True
cal_db_interface = "tcp://max-exfl016:8020" # calibration DB interface to use
cal_db_timeout = 300000 # timeout on caldb requests
db_output = False # Output constants to the calibration database
local_output = True # output constants locally

number_dark_frames = 0 # number of images to be used, if set to 0 all available images are used
temp_limits = 5 # limit for parameter Operational temperature
db_module = 'ePix100_M17' # detector karabo_id
bias_voltage = 200 # bias voltage
in_vacuum = False # detector operated in vacuum
fix_temperature = 290. # fix temperature to this value

In [ ]:
from IPython.display import display, Markdown, Latex
import os
import textwrap

import numpy as np
import h5py
import matplotlib.pyplot as plt
%matplotlib inline
import warnings
warnings.filterwarnings('ignore')

from cal_tools.tools import get_dir_creation_date, save_const_to_h5, get_random_db_interface
from iCalibrationDB import (ConstantMetaData, Constants, Conditions, Detectors,
                            Versions)
from iCalibrationDB.detectors import DetectorTypes
import XFELDetAna.xfelprofiler as xprof
profiler = xprof.Profiler()
profiler.disable()
from XFELDetAna.util import env
env.iprofile = cluster_profile
from XFELDetAna import xfelpycaltools as xcal
from XFELDetAna import xfelpyanatools as xana
from XFELDetAna.plotting.util import prettyPlotting
prettyPlotting = True
from XFELDetAna.xfelreaders import ChunkReader
from XFELDetAna.detectors.fastccd import readerh5 as fastccdreaderh5

h5path = h5path.format(karabo_id, receiver_id)
h5path_t = h5path_t.format(karabo_id, receiver_id)
h5path_cntrl = h5path_cntrl.format(karabo_id)

def nImagesOrLimit(nImages, limit):
    if limit == 0:
        return nImages
    else:
        return min(nImages, limit)

In [ ]:
proposal = list(filter(None, in_folder.strip('/').split('/')))[-2]
file_loc = f'proposal:{proposal} runs:{run}'

x = 708  # rows of the xPix100
y = 768  # columns of the xPix100

ped_dir = os.path.join(in_folder, f"r{run:04d}")
fp_name = path_template.format(run, karabo_da[0]).format(sequence)
filename = os.path.join(ped_dir, fp_name)

print(f"Reading data from: {filename}\n")
print(f"Run number: {run}")
print(f"HDF5 path: {h5path}")
if use_dir_creation_date:
    creation_time = get_dir_creation_date(in_folder, run)
    print(f"Using {creation_time.isoformat()} as creation time")
os.makedirs(out_folder, exist_ok=True)

In [ ]:
sensorSize = [x, y]
chunkSize = 100  #Number of images to read per chunk

#Sensor area will be analysed according to blocksize
blockSize = [sensorSize[0] // 2, sensorSize[1] // 2]
xcal.defaultBlockSize = blockSize
cpuCores = 4  #Specifies the number of running cpu cores
memoryCells = 1  #No mamery cells

#Specifies total number of images to proceed
nImages = fastccdreaderh5.getDataSize(filename, h5path)[0]
nImages = nImagesOrLimit(nImages, number_dark_frames)
print("\nNumber of dark images to analyze: ", nImages)
run_parallel = False

with h5py.File(filename, 'r') as f:
    integration_time = int(f[os.path.join(h5path_cntrl, "CONTROL","expTime", "value")][0])
    temperature = np.mean(f[h5path_t])/100.
    temperature_k = temperature + 273.15
    if fix_temperature != 0:
        temperature_k = fix_temperature
        print("Temperature is fixed!")
    print(f"Bias voltage is {bias_voltage} V")
    print(f"Detector integration time is set to {integration_time}")
    print(f"Mean temperature was {temperature:0.2f} °C / {temperature_k:0.2f} K")
    print(f"Operated in vacuum: {in_vacuum} ")

In [ ]:
reader = ChunkReader(filename, fastccdreaderh5.readData,
                     nImages, chunkSize,
                     path=h5path,
                     pixels_x=sensorSize[0],
                     pixels_y=sensorSize[1], )


In [ ]:
noiseCal = xcal.NoiseCalculator(sensorSize, memoryCells,
                                cores=cpuCores, blockSize=blockSize,
                                parallel=run_parallel)
histCalRaw = xcal.HistogramCalculator(sensorSize, bins=1000,
                                      range=[0, 10000], parallel=False,
                                      memoryCells=memoryCells,
                                      cores=cpuCores, blockSize=blockSize)


In [ ]:
for data in reader.readChunks():
    dx = np.count_nonzero(data, axis=(0, 1))
    data = data[:, :, dx != 0]
    histCalRaw.fill(data)
    noiseCal.fill(data) #Fill calculators with data
    
constant_maps = {}
constant_maps['Offset'] = noiseCal.getOffset()  #Produce offset map
constant_maps['Noise'] = noiseCal.get()  #Produce noise map

noiseCal.reset()  #Reset noise calculator
print("Initial maps were created")


In [ ]:
#**************OFFSET MAP HISTOGRAM***********#
ho, co = np.histogram(constant_maps['Offset'].flatten(), bins=700)

do = {'x': co[:-1],
      'y': ho,
      'y_err': np.sqrt(ho[:]),
      'drawstyle': 'bars',
      'color': 'cornflowerblue',
      }

fig = xana.simplePlot(do, figsize='1col', aspect=2,
                      x_label='Offset (ADU)',
                      y_label="Counts", y_log=True,
                      )

#*****NOISE MAP HISTOGRAM FROM THE OFFSET CORRECTED DATA*******#
hn, cn = np.histogram(constant_maps['Noise'].flatten(), bins=200)

dn = {'x': cn[:-1],
      'y': hn,
      'y_err': np.sqrt(hn[:]),
      'drawstyle': 'bars',
      'color': 'cornflowerblue',
      }

fig = xana.simplePlot(dn, figsize='1col', aspect=2,
                      x_label='Noise (ADU)',
                      y_label="Counts",
                      y_log=True)

#**************HEAT MAPS*******************#
fig = xana.heatmapPlot(constant_maps['Offset'][:, :, 0],
                       x_label='Columns', y_label='Rows',
                       lut_label='Offset (ADU)',
                       x_range=(0, y),
                       y_range=(0, x), vmin=1000, vmax=4000)

fig = xana.heatmapPlot(constant_maps['Noise'][:, :, 0],
                       x_label='Columns', y_label='Rows',
                       lut_label='Noise (ADU)',
                       x_range=(0, y),
                       y_range=(0, x), vmax=2 * np.mean(constant_maps['Noise']))


In [ ]:
# Save constants to DB
dclass="ePix100"
cal_db_interface = get_random_db_interface(cal_db_interface)
for const_name in constant_maps.keys():
    metadata = ConstantMetaData()
    det = getattr(Constants, dclass)
    const = getattr(det, const_name)()
    const.data = constant_maps[const_name].data

    metadata.calibration_constant = const

    # set the operating condition
    dcond = Conditions.Dark
    condition =  getattr(dcond, dclass)(bias_voltage=bias_voltage,
                                        integration_time=integration_time,
                                        temperature=temperature_k,
                                        in_vacuum=in_vacuum)

    for parm in condition.parameters:
        if parm.name == "Sensor Temperature":
            parm.lower_deviation = temp_limits
            parm.upper_deviation = temp_limits

    device = getattr(Detectors, db_module)
    metadata.detector_condition = condition

    # specify the a version for this constant
    if creation_time is None:
        metadata.calibration_constant_version = Versions.Now(device=device)
    else:
        metadata.calibration_constant_version = Versions.Timespan(device=device,
                                                                  start=creation_time)
        
    metadata.calibration_constant_version.raw_data_location = file_loc

    if db_output:
        try:
            metadata.send(cal_db_interface, timeout=cal_db_timeout)
            print(f"Inject {const_name} constants from {metadata.calibration_constant_version.begin_at}\n")
        except Exception as e:    
            if "has already been take" in str(e):
                print(f"{const_name} has already been injected with the same parameter conditions\n")
            else:
                # To prevent having big error message in the pdf report.
                print("\n".join(textwrap.wrap(str(e),100)))

    if local_output:
        save_const_to_h5(metadata, out_folder)
        print(f"Calibration constant {const_name} is stored locally at {out_folder}.")

print(f"Operating conditions are:\n• Bias voltage: {bias_voltage}\n• Integration time: {integration_time}\n"
      f"• Temperature: {temperature_k}\n• In Vacuum: {in_vacuum}\n"
      f"• Creation time: {metadata.calibration_constant_version.begin_at}\n")